# Pull and manipulate the API data

The point of this exercise is to try data enrichment with data from external APIs. We are going to take data about road kills in Vermont in 2006 and try to figure out the weather during the accident and how many bars there are in the area. We will work with one api that has a Python wrapper library and one that does not.



## Data

The data for this exercise can be found [here](https://drive.google.com/file/d/1Nk-5RZC1yzJl7HzOJd3tzUjzMENSSdJJ/view?usp=sharing).

Just run the cells below to get your data ready. Little help from us.


In [169]:
import pandas as pd
mypath = "/home/itod/Desktop/basecamp_spring_2019/itodorovic/data/"

In [173]:
data = pd.read_csv(mypath + "VT_VehicleAnimal_Collisions__2006.csv", 
                   na_values=['', ' '],
                   parse_dates=["DATE_"]
                  )
data["MONTH_"] = data.DATE_.dt.month
data.dropna(subset=['X', 'Y'], inplace=True)
data['ll'] = data['Y'].astype(str) + ',' + data['X'].astype(str)
print(data.shape)
data.head()

(2244, 23)


X          Y  OBJECTID   MSRI_CODE  \
4 -72.989424  42.833309         5        Deer   
5 -72.375495  43.581005         6  Deer RK AB   
6 -72.840257  43.235023         7     Lg Bird   
7 -72.830991  44.783002         8       Otter   
9 -72.514595  44.242323        10      Beaver   

                                  MSRI_DESCR      DATE_  TOWN_ID ROUTE_DES  \
4                                       Deer 2004-04-16    209.0      VT 8   
5                 Deer, RoadKill, Adult Buck 2005-03-22   1409.0      US 5   
6  Large Bird (hawk, owl, turkey, waterfowl) 2004-11-15   1310.0     VT 11   
7                                      Otter 2004-10-18    601.0     VT 36   
9                                     Beaver 2005-04-22   1207.0      US 2   

  ROUTE  BEGIN_MM                  ...                            TOWN  \
4   008      0.35                  ...                       READSBORO   
5   005      5.00                  ...                        HARTLAND   
6   011      0.50                  ...                     LONDONDERRY   
7   036      1.00                  ...                     BAKERSFIELD   
9   002      0.19                  ...                    EAST MONTPEL   

  RT_TOWN RT_NUM DAY_  MONTH_  YEAR_  REP_AGEN  LOCATION  YEAR_INT  \
4     NaN    NaN  NaN     4.0   2004       AOT       NaN      2004   
5     NaN    NaN  NaN     3.0   2005       AOT       NaN      2005   
6     NaN    NaN  NaN    11.0   2004       AOT       NaN      2004   
7     NaN    NaN  NaN    10.0   2004       AOT       NaN      2004   
9     NaN    NaN  NaN     4.0   2005       AOT       NaN      2005   

                                      ll  
4   42.83330874047745,-72.98942388725152  
5  43.581005107295645,-72.37549549789222  
6    43.23502288333559,-72.8402568531839  
7   44.78300220380285,-72.83099079061695  
9   44.24232301744294,-72.51459452575021  

[5 rows x 23 columns]

## Foursquare API

Foursquare API documentation is [here](https://developer.foursquare.com/)

1. Start a foursquare application and get your keys.
2. For each crush, pull number of of bars (category "Nightlife") in 5km radius.
3. Find a relationship between number of bars in the area and severity of the crash.
4. (optional) Try to come up with other approaches to get more information out of the data. 
5. (optional) Think about the most generic way to approach the problem.

Hints:

* check out python package "foursquare"
* what happens if the code fails?
* what if you run out of requests? (check out [time](https://docs.python.org/2/library/time.html) package)

In [16]:
#set the keys
foursquare_id = "B1C144JU4YV5KOTLC4BY0QEXPSYWPCTXUN1NOU3CMYNRQVU2"
foursquare_secret = "FOXGD24MZWVHIA0C3BBIDF00ZMKYNNSM0QAC0IF4H5ODEGO5"

In [131]:
#install and load the library
import foursquare
from foursquare import FoursquareException

# Construct the client object
client = foursquare.Foursquare(client_id=foursquare_id, client_secret=foursquare_secret, redirect_uri='http://fondu.com/oauth/authorize')

# Build the authorization url for your app
auth_uri = client.oauth.auth_url()

In [132]:
#declare the client
def get_venues(ll):
    params = {'intent': 'browse',
          'categoryId': '4d4b7105d754a06376d81259',
          'radius': 5000,
          'limit': 50}
    params['ll']=ll
    
    try:
        result = client.venues.search(params=params)
        return len(result['venues'])
    except FoursquareException as e:
        print(e)
        return -1

#get_venues('48.146394, 17.107969')

In [ ]:
data['ll'] = data['Y'].astype(str) + ',' + data['X'].astype(str)

for ind, row in data.iterrows():
    print(get_venues(row['ll']))

## DarkSky API

DarkSky API documentation is [here](https://darksky.net/dev/docs/time-machine)

1. Sign up for FREE api key.
2. For each crush, get the weather for the location and time.
3. Find a relationship between the weather and severity of the crash.

Hints:

* randomly sample only 500 or so (due to API limits)
* use "Time Machine" request in DarkSky API
* for sending HTTP requests check out "requests" library [here](http://docs.python-requests.org/en/master/)



In [193]:
import requests
import time
api_key = "bb7c474338ee56898672d089fb85ced8"

In [195]:
# how many unique towns we have, to try to go under API limits
print(data['TOWN_ID'].nunique())

106


In [437]:
import numpy as np
import datetime
#towns = data.groupby('TOWN_ID').min()
#towns['timestamp'] = (pd.DatetimeIndex(towns['DATE_']).astype(np.int64)/1000000).astype(np.int64)
data['TOWN'] = data['TOWN'].str.upper()
towns = data.groupby(['TOWN','DATE_'])['X','Y'].mean()
towns['ll'] = towns['Y'].astype(str) + ',' + towns['X'].astype(str)
towns = towns.reset_index()

In [446]:
towns.shape

(2105, 5)

In [338]:
base_url = 'https://api.darksky.net/forecast/'
ll = '43.581617569506605,-72.51483075364598'
time_only = 'T00:00:00'
sufix = '?exclude=currently,flags'

In [334]:
resp = requests.get(base_url + api_key + '/' + ll + ',' + '2004-04-13' + time_only + sufix)

In [393]:
df = pd.DataFrame(resp.json()['daily']['data'][0], index=[0])

time                                 summary  icon  sunriseTime  \
0  1081828800  Heavy rain in the morning and evening.  rain   1081851094   

   sunsetTime  moonPhase  precipIntensity  precipIntensityMax  \
0  1081899240        0.8           0.0279              0.3211   

   precipIntensityMaxTime  precipProbability             ...              \
0              1081904400                  1             ...               

  uvIndexTime  visibility  temperatureMin  temperatureMinTime  temperatureMax  \
0  1081868400         7.6           34.16          1081850400           40.76   

   temperatureMaxTime  apparentTemperatureMin  apparentTemperatureMinTime  \
0          1081911600                   34.16                  1081850400   

   apparentTemperatureMax  apparentTemperatureMaxTime  
0                   40.76                  1081911600  

[1 rows x 38 columns]

In [455]:
batch = []
batch.append(towns.iloc[0:489, :])
batch.append(towns.iloc[490:879, :])
batch.append(towns.iloc[880:1269, :])
batch.append(towns.iloc[1270:1659, :])
batch.append(towns.iloc[1660:, :])

TOWN             object
DATE_    datetime64[ns]
X               float64
Y               float64
ll               object
dtype: object

In [465]:
df_api = pd.DataFrame()

# we only use first 490 rows from original dataframe
tmp = batch[0]

for ind, row in tmp.iterrows():
    req_str = base_url + api_key + '/' + row['ll'] + ',' + str(row['DATE_'])[:-9] + time_only + sufix
    resp = requests.get(req_str)
    print(resp.json())
    try:
        weather = resp.json()['daily']['data'][0]
        df_api = df_api.append(pd.DataFrame(weather, index = [ind]))
        print(weather)
    except:
        pass


{'latitude': 44.03603367456014, 'longitude': -73.41895683118159, 'timezone': 'America/New_York', 'offset': -4}
{'latitude': 44.095871380936586, 'longitude': -73.30033208392106, 'timezone': 'America/New_York', 'hourly': {'summary': 'Clear throughout the day.', 'icon': 'clear-day', 'data': [{'time': 957326400, 'summary': 'Clear', 'icon': 'clear-night', 'precipIntensity': 0, 'precipProbability': 0, 'temperature': 41.33, 'apparentTemperature': 41.33, 'dewPoint': 28.95, 'humidity': 0.61, 'pressure': 1023.1, 'windSpeed': 0, 'cloudCover': 0, 'uvIndex': 0, 'visibility': 10}, {'time': 957330000, 'summary': 'Clear', 'icon': 'clear-night', 'precipIntensity': 0, 'precipProbability': 0, 'temperature': 39.34, 'apparentTemperature': 39.34, 'dewPoint': 28.95, 'humidity': 0.66, 'pressure': 1023.51, 'windSpeed': 0, 'cloudCover': 0, 'uvIndex': 0, 'visibility': 10}, {'time': 957333600, 'summary': 'Clear', 'icon': 'clear-night', 'precipIntensity': 0, 'precipProbability': 0, 'temperature': 38.26, 'apparentT

In [402]:
print(df_api.shape)
print(towns.shape)

(358, 39)
(358, 5)


In [403]:
towns.drop(['X', 'Y', 'll'], inplace = True, axis = 1)

In [407]:
towns = towns.merge(df_api, how='outer', left_index=True, right_index=True)

In [408]:
towns.head()

TOWN_ID      DATE_  apparentTemperatureHigh  apparentTemperatureHighTime  \
0    107.0 2004-04-13                    38.31                   1081893600   
1    108.0 2004-09-16                    72.36                   1095361200   
2    201.0 2004-06-18                    79.49                   1087596000   
3    202.0 2004-02-06                    30.16                   1076112000   
4    202.0 2004-06-16                    80.19                   1087423200   

   apparentTemperatureLow  apparentTemperatureLowTime  apparentTemperatureMax  \
0                   38.46                  1081900800                   40.76   
1                   59.42                  1095415200                   72.36   
2                   65.38                  1087646400                   79.49   
3                   29.65                  1076148000                   35.45   
4                   60.23                  1087462800                   80.19   

   apparentTemperatureMaxTime  apparentTemperatureMin  \
0                  1081911600                   34.16   
1                  1095361200                   51.32   
2                  1087596000                   64.94   
3                  1076115600                   16.92   
4                  1087423200                   53.60   

   apparentTemperatureMinTime    ...      temperatureMin  temperatureMinTime  \
0                  1081850400    ...               34.16          1081850400   
1                  1095332400    ...               51.32          1095332400   
2                  1087552800    ...               64.33          1087552800   
3                  1076076000    ...               21.72          1076065200   
4                  1087380000    ...               53.60          1087380000   

         time uvIndex  uvIndexTime  visibility  windBearing  windGust  \
0  1081828800       4   1081868400        7.60        157.0     21.02   
1  1095307200       6   1095350400        8.80        191.0     12.01   
2  1087531200      10   1087574400        9.21        158.0     10.99   
3  1076043600       2   1076083200        5.70         95.0     24.17   
4  1087358400      10   1087401600        8.89        265.0      7.99   

   windGustTime  windSpeed  
0  1.081879e+09       1.72  
1  1.095358e+09       0.80  
2  1.087582e+09       1.52  
3  1.076094e+09       3.31  
4  1.087405e+09       0.60  

[5 rows x 41 columns]

In [412]:
print(data.shape)
print(towns.shape)

(2244, 23)
(358, 41)


In [414]:
data.head()

X          Y  OBJECTID   MSRI_CODE  \
4 -72.989424  42.833309         5        Deer   
5 -72.375495  43.581005         6  Deer RK AB   
6 -72.840257  43.235023         7     Lg Bird   
7 -72.830991  44.783002         8       Otter   
9 -72.514595  44.242323        10      Beaver   

                                  MSRI_DESCR      DATE_  TOWN_ID ROUTE_DES  \
4                                       Deer 2004-04-16    209.0      VT 8   
5                 Deer, RoadKill, Adult Buck 2005-03-22   1409.0      US 5   
6  Large Bird (hawk, owl, turkey, waterfowl) 2004-11-15   1310.0     VT 11   
7                                      Otter 2004-10-18    601.0     VT 36   
9                                     Beaver 2005-04-22   1207.0      US 2   

  ROUTE  BEGIN_MM                  ...                            TOWN  \
4   008      0.35                  ...                       READSBORO   
5   005      5.00                  ...                        HARTLAND   
6   011      0.50                  ...                     LONDONDERRY   
7   036      1.00                  ...                     BAKERSFIELD   
9   002      0.19                  ...                    EAST MONTPEL   

  RT_TOWN RT_NUM DAY_  MONTH_  YEAR_  REP_AGEN  LOCATION  YEAR_INT  \
4     NaN    NaN  NaN     4.0   2004       AOT       NaN      2004   
5     NaN    NaN  NaN     3.0   2005       AOT       NaN      2005   
6     NaN    NaN  NaN    11.0   2004       AOT       NaN      2004   
7     NaN    NaN  NaN    10.0   2004       AOT       NaN      2004   
9     NaN    NaN  NaN     4.0   2005       AOT       NaN      2005   

                                      ll  
4   42.83330874047745,-72.98942388725152  
5  43.581005107295645,-72.37549549789222  
6    43.23502288333559,-72.8402568531839  
7   44.78300220380285,-72.83099079061695  
9   44.24232301744294,-72.51459452575021  

[5 rows x 23 columns]

In [416]:
towns.head()

TOWN_ID      DATE_  apparentTemperatureHigh  apparentTemperatureHighTime  \
0    107.0 2004-04-13                    38.31                   1081893600   
1    108.0 2004-09-16                    72.36                   1095361200   
2    201.0 2004-06-18                    79.49                   1087596000   
3    202.0 2004-02-06                    30.16                   1076112000   
4    202.0 2004-06-16                    80.19                   1087423200   

   apparentTemperatureLow  apparentTemperatureLowTime  apparentTemperatureMax  \
0                   38.46                  1081900800                   40.76   
1                   59.42                  1095415200                   72.36   
2                   65.38                  1087646400                   79.49   
3                   29.65                  1076148000                   35.45   
4                   60.23                  1087462800                   80.19   

   apparentTemperatureMaxTime  apparentTemperatureMin  \
0                  1081911600                   34.16   
1                  1095361200                   51.32   
2                  1087596000                   64.94   
3                  1076115600                   16.92   
4                  1087423200                   53.60   

   apparentTemperatureMinTime    ...      temperatureMin  temperatureMinTime  \
0                  1081850400    ...               34.16          1081850400   
1                  1095332400    ...               51.32          1095332400   
2                  1087552800    ...               64.33          1087552800   
3                  1076076000    ...               21.72          1076065200   
4                  1087380000    ...               53.60          1087380000   

         time uvIndex  uvIndexTime  visibility  windBearing  windGust  \
0  1081828800       4   1081868400        7.60        157.0     21.02   
1  1095307200       6   1095350400        8.80        191.0     12.01   
2  1087531200      10   1087574400        9.21        158.0     10.99   
3  1076043600       2   1076083200        5.70         95.0     24.17   
4  1087358400      10   1087401600        8.89        265.0      7.99   

   windGustTime  windSpeed  
0  1.081879e+09       1.72  
1  1.095358e+09       0.80  
2  1.087582e+09       1.52  
3  1.076094e+09       3.31  
4  1.087405e+09       0.60  

[5 rows x 41 columns]

In [428]:
df_merged = data.merge(towns, how = 'left', on = ['TOWN_ID', 'DATE_'])

In [426]:
data.dtypes

X                    float64
Y                    float64
OBJECTID               int64
MSRI_CODE             object
MSRI_DESCR            object
DATE_         datetime64[ns]
TOWN_ID              float64
ROUTE_DES             object
ROUTE                 object
BEGIN_MM             float64
END_MM               float64
LRS_CODE              object
COMMENT               object
TOWN                  object
RT_TOWN              float64
RT_NUM               float64
DAY_                 float64
MONTH_               float64
YEAR_                  int64
REP_AGEN              object
LOCATION              object
YEAR_INT               int64
ll                    object
dtype: object

In [425]:
towns.dtypes

TOWN_ID                               float64
DATE_                          datetime64[ns]
apparentTemperatureHigh               float64
apparentTemperatureHighTime             int64
apparentTemperatureLow                float64
apparentTemperatureLowTime              int64
apparentTemperatureMax                float64
apparentTemperatureMaxTime              int64
apparentTemperatureMin                float64
apparentTemperatureMinTime              int64
cloudCover                            float64
dewPoint                              float64
humidity                              float64
icon                                   object
moonPhase                             float64
precipAccumulation                    float64
precipIntensity                       float64
precipIntensityMax                    float64
precipIntensityMaxTime                float64
precipProbability                     float64
precipType                             object
pressure                          

In [429]:
df_merged.shape

(2244, 62)

In [432]:
data.count()

X             2244
Y             2244
OBJECTID      2244
MSRI_CODE     2244
MSRI_DESCR     419
DATE_         2205
TOWN_ID        419
ROUTE_DES      419
ROUTE          419
BEGIN_MM      2244
END_MM        2244
LRS_CODE       419
COMMENT        304
TOWN          2244
RT_TOWN          0
RT_NUM           0
DAY_          1825
MONTH_        2205
YEAR_         2244
REP_AGEN      2244
LOCATION      1821
YEAR_INT      2244
ll            2244
dtype: int64

In [431]:
df_merged

X          Y  OBJECTID   MSRI_CODE  \
0    -72.989424  42.833309         5        Deer   
1    -72.375495  43.581005         6  Deer RK AB   
2    -72.840257  43.235023         7     Lg Bird   
3    -72.830991  44.783002         8       Otter   
4    -72.514595  44.242323        10      Beaver   
5    -73.195801  43.433986        12     Lg Bird   
6    -72.904462  44.807817        13       Otter   
7    -72.393480  43.462770        17       Other   
8    -72.842383  44.785350        19       Other   
9    -72.515176  44.172910        21  Deer RK AD   
10   -72.964792  43.555489        23  Deer RK AD   
11   -72.830575  43.234067        25  Deer RK AD   
12   -72.388508  43.496862        29  Deer RK AD   
13   -72.721540  44.423275        30        Deer   
14   -72.963633  43.569823        31       Other   
15   -72.957238  44.899844        33       Other   
16   -73.203575  43.776861        36  Deer RK AD   
17   -72.712001  44.473911        47        Deer   
18   -72.985410  42.826518        48        Deer   
19   -73.079308  44.779723        51       Otter   
20   -72.451960  43.606004        53  Deer RK FB   
21   -72.518030  43.457710        58       Other   
22   -72.957837  43.539738        60  Deer RK AB   
23   -73.097819  44.879109        61       Other   
24   -72.209183  43.898627        62       Other   
25   -73.104315  44.922906        63       Other   
26   -72.649046  44.115782        65       Other   
27   -72.448879  43.467289        66       Other   
28   -72.567593  44.338097        68  Deer RK FD   
29   -72.987662  42.828544        70  Deer RK AB   
...         ...        ...       ...         ...   
2214 -72.044862  44.840422      1971       Moose   
2215 -72.064937  44.835181      1972       Moose   
2216 -72.064936  44.835105      1973       Moose   
2217 -72.064609  44.835649      1974       Moose   
2218 -72.051025  44.859371      1975       Moose   
2219 -72.064673  44.835568      1976       Moose   
2220 -72.064793  44.835408      1977       Moose   
2221 -72.063552  44.837136      1978       Moose   
2222 -72.053205  44.855165      1979       Moose   
2223 -71.958558  44.816976      1980       Moose   
2224 -71.966512  44.818216      1981       Moose   
2225 -71.946863  44.814238      1982       Moose   
2226 -72.037498  44.862104      1983       Moose   
2227 -72.035991  44.860602      1984       Moose   
2228 -72.023292  44.848895      1985       Moose   
2229 -72.010253  44.843170      1986       Moose   
2230 -72.172965  44.876404      1987       Moose   
2231 -72.172390  44.886088      1988       Moose   
2232 -72.243611  44.900773      1989       Moose   
2233 -72.405002  44.649490      1990       Moose   
2234 -72.175957  44.901331      1991       Moose   
2235 -72.177261  44.911458      1992       Moose   
2236 -72.175998  44.915333      1993       Moose   
2237 -72.175776  44.915756      1994       Moose   
2238 -72.187429  44.861572      1995       Moose   
2239 -72.173565  44.920438      1996       Moose   
2240 -72.175704  44.918044      1997       Moose   
2241 -72.178881  44.907688      1998       Moose   
2242 -72.171270  44.927490      1999       Moose   
2243 -72.161917  44.939564      2000       Moose   

                                     MSRI_DESCR      DATE_  TOWN_ID ROUTE_DES  \
0                                          Deer 2004-04-16    209.0      VT 8   
1                    Deer, RoadKill, Adult Buck 2005-03-22   1409.0      US 5   
2     Large Bird (hawk, owl, turkey, waterfowl) 2004-11-15   1310.0     VT 11   
3                                         Otter 2004-10-18    601.0     VT 36   
4                                        Beaver 2005-04-22   1207.0      US 2   
5     Large Bird (hawk, owl, turkey, waterfowl) 2005-04-06   1126.0     VT 30   
6                                         Otter 2004-10-04    605.0     VT 36   
7                                         Other 2005-12-20   1423.0      US 5   
8                                         Other 2005-06-09  